## Compute clusters of poor service

This notebook computes clusters of poor service using local Moran's local indicators of spatial association

Before running this notebook, you will need to:

- record data
- construct `dataset.parquet` and `stations_geo.geojson` with [`Build dataset`](../Build%20dataset.ipynb)
- construct `stations_service_measures.geojson` with [`Build service measures`](Build%20service%20measures.ipynb)

In [1]:
import pandas as pd
import geopandas as gpd
import numpy as np

from libpysal.weights import DistanceBand
from esda import Moran_Local

from concave_hull import concave_hull
from shapely import Polygon

import seaborn as sns
sns.set_style('whitegrid')


In [2]:
QUADRANT_LABELS = {
    1:'HH',
    2:'LH',
    3:'LL',
    4:'HL'
}

In [3]:
!pip list

Package                       Version
----------------------------- --------
altair                        5.0.1
asttokens                     2.2.1
attrs                         23.1.0
backcall                      0.2.0
backports.functools-lru-cache 1.6.4
beautifulsoup4                4.12.2
branca                        0.6.0
certifi                       2024.2.2
charset-normalizer            3.1.0
click                         8.1.3
click-default-group-wheel     1.2.2
click-plugins                 1.1.1
cligj                         0.7.2
colorama                      0.4.6
comm                          0.1.3
concave-hull                  0.0.6
contourpy                     1.0.7
cramjam                       2.6.2
cycler                        0.11.0
debugpy                       1.6.7
decorator                     5.1.1
esda                          2.5.1
et-xmlfile                    1.1.0
executing                     1.2.0
fastparquet                   2023.4.0
Fiona         

read in data

In [4]:
stations_service_measures = (
    gpd.read_file('../stations_service_measures.geojson')
    .set_index('station_id')
)

In [5]:
stations_service_measures.head()

freq_am_or_evening_no_bikes_or_no_docks   
station_id                                                                      
66dc2995-0aca-11e7-82f6-3863bb44ef7c                                 0.164087  \
06439006-11b6-44f0-8545-c9d39035f32a                                 1.000000   
19d17911-1e4a-41fa-b62b-719aa0a6182e                                 1.000000   
1861678548643203686                                                  0.000000   
cd2d9dab-7708-4685-a56f-9412c738de7e                                 0.260062   

                                      pct_of_docks_w_disabled_bikes_median   
station_id                                                                   
66dc2995-0aca-11e7-82f6-3863bb44ef7c                              0.019608  \
06439006-11b6-44f0-8545-c9d39035f32a                              0.000000   
19d17911-1e4a-41fa-b62b-719aa0a6182e                              0.000000   
1861678548643203686                                               0.080000   
cd2d9dab-7708-4685-a56f-9412c738de7e                              0.000000   

                                      pct_of_docks_w_disabled_bikes_mean   
station_id                                                                 
66dc2995-0aca-11e7-82f6-3863bb44ef7c                            0.028670  \
06439006-11b6-44f0-8545-c9d39035f32a                            0.000000   
19d17911-1e4a-41fa-b62b-719aa0a6182e                            0.000000   
1861678548643203686                                             0.112293   
cd2d9dab-7708-4685-a56f-9412c738de7e                            0.014316   

                                      zero_daytime_duration_max   
station_id                                                        
66dc2995-0aca-11e7-82f6-3863bb44ef7c                   0.966944  \
06439006-11b6-44f0-8545-c9d39035f32a                   0.000000   
19d17911-1e4a-41fa-b62b-719aa0a6182e                   0.000000   
1861678548643203686                                    0.000000   
cd2d9dab-7708-4685-a56f-9412c738de7e                   4.913333   

                                      zero_daytime_duration_mean   
station_id                                                         
66dc2995-0aca-11e7-82f6-3863bb44ef7c                    0.966944  \
06439006-11b6-44f0-8545-c9d39035f32a                    0.000000   
19d17911-1e4a-41fa-b62b-719aa0a6182e                    0.000000   
1861678548643203686                                     0.000000   
cd2d9dab-7708-4685-a56f-9412c738de7e                    2.183235   

                                      zero_daytime_duration_median   
station_id                                                           
66dc2995-0aca-11e7-82f6-3863bb44ef7c                      0.966944  \
06439006-11b6-44f0-8545-c9d39035f32a                      0.000000   
19d17911-1e4a-41fa-b62b-719aa0a6182e                      0.000000   
1861678548643203686                                       0.000000   
cd2d9dab-7708-4685-a56f-9412c738de7e                      2.183611   

                                                        geometry  
station_id                                                        
66dc2995-0aca-11e7-82f6-3863bb44ef7c  POINT (-73.99145 40.74395)  
06439006-11b6-44f0-8545-c9d39035f32a  POINT (-74.01047 40.71222)  
19d17911-1e4a-41fa-b62b-719aa0a6182e  POINT (-74.00522 40.71979)  
1861678548643203686                   POINT (-73.88300 40.84784)  
cd2d9dab-7708-4685-a56f-9412c738de7e  POINT (-73.93618 40.66034)

In [6]:
stations_service_measures.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

project to local projection for accurate local distance measures

In [7]:
stations_service_measures = stations_service_measures.to_crs(2263)

remove NJ and islands

(create network of stations within 1/2 mile distance. remove stations not in _main_ component)

In [8]:
w_threshold = DistanceBand.from_dataframe(
    stations_service_measures,
    threshold=2640,
    binary=True
)

c:\Users\dlevine\Anaconda3\envs\citibike-analysis\Lib\site-packages\libpysal\weights\weights.py:224: UserWarning: The weights matrix is not fully connected: 
 There are 5 disconnected components.
 There is 1 island with id: 66dd5e69-0aca-11e7-82f6-3863bb44ef7c.
  warnings.warn(message)


In [9]:
(
    stations_service_measures
    .assign(
        component = w_threshold.component_labels
    )
    .explore(
        tiles='cartodb positron',
        column='component',
        legend=True,
        categorical=True
    )
)

drop Governor's Island and NJ

In [10]:
stations_service_measures = (
    stations_service_measures
    .loc[w_threshold.component_labels == 0]
)

## compute poor service clusters

Create spatial weights matrix. 

Use inverse square distance decay

In [11]:
w_idw = DistanceBand.from_dataframe(
    stations_service_measures,
    threshold=2640,
    binary=False,
    alpha=-2
)

c:\Users\dlevine\Anaconda3\envs\citibike-analysis\Lib\site-packages\scipy\sparse\_data.py:117: RuntimeWarning: divide by zero encountered in power
  return self._with_data(data ** n)


In [12]:
w_idw.set_transform('r')

In [13]:
measures = [
    'freq_am_or_evening_no_bikes_or_no_docks',
    'zero_daytime_duration_median',
    'pct_of_docks_w_disabled_bikes_median',
]

Check for missing values. 

LISA cannot be computed over missing values. Fill NaNs, or remove NaNs then recompute the weights matrix with only the remaining rows.

In [14]:
stations_service_measures[measures].isna().any()

freq_am_or_evening_no_bikes_or_no_docks    False
zero_daytime_duration_median               False
pct_of_docks_w_disabled_bikes_median       False
dtype: bool

For each focus measure, compute local Moran's local indicators of spatial association across all station locations. label stations as significant high-high or low-low clusters if they are in these quadrants and are significant at the alpha threshold

In [15]:
alpha = 0.01

In [16]:
local_moran_results = []

for measure in measures:
  
    measure_local_moran = Moran_Local(
        y=stations_service_measures[measure],
        w=w_idw,
        transformation='r',
        permutations=1000,
        n_jobs=-1,
        seed=1
    )

    measure_result = (
        stations_service_measures
        [[measure]]
        .assign(
            q = measure_local_moran.q,
            p_z_sim = measure_local_moran.p_z_sim,
            p_sim = measure_local_moran.p_sim,
            significant_cluster = lambda row: (
                row['q'].map(QUADRANT_LABELS)
                .where(
                    (row['p_z_sim'] < alpha) & 
                    (row['q'].isin([1,3]))
                )
            ),
        )
        .rename(columns={
            'q':f'{measure}_q',
            'p_z_sim':f'{measure}_p_z_sim',
            'p_sim':f'{measure}_p_sim',
            'significant_cluster':f'{measure}_significant_cluster',
        })
    )

    local_moran_results.append(measure_result)


combine the local indicators across all focus measures and assign an 'any_high_high' label if the station is in any significant high-high cluster for any measure

In [17]:
local_moran_by_measure = (
    stations_service_measures[['geometry']]
    .join(
        pd.concat(
            local_moran_results, 
            axis=1
        ),
        how='left'
    )
    .assign(
        any_high_high = lambda row: (
            row
            .filter(like='significant_cluster')
            .eq('HH')
            .any(axis=1)
        )
    )
)

peek at results

In [18]:
(
    local_moran_by_measure
    .explore(
        tiles='cartodb positron nolabels',
        column='any_high_high',
        cmap=['#4f84bd','#f03813'],
        marker_kwds=dict(
            radius=1
        )
    )
)

### filter to stations within clusters of 5 or more and draw boundaries around clusters

In [19]:
poor_service_stations = (
    local_moran_by_measure
    [
        local_moran_by_measure['any_high_high'] == True
    ]
)

Group poor service stations into subnetworks of all poor serivce stations within 1/4 mile or one another. drop groups with fewer than 5 stations.

In [20]:
w_split_at_1320 = DistanceBand.from_dataframe(
    df=poor_service_stations,
    threshold=1320,
    binary=True
)

poor_service_stations = (
    poor_service_stations
    .assign(
        component = w_split_at_1320.component_labels
    )
)

poor_service_stations__component_5_or_more_nodes = (
    poor_service_stations
    [
        poor_service_stations
        ['component']
        .isin(
            poor_service_stations
            ['component']
            .value_counts()
            .ge(5)
            .where(lambda a:a).dropna()
            .index
        )
    ]
)

c:\Users\dlevine\Anaconda3\envs\citibike-analysis\Lib\site-packages\libpysal\weights\weights.py:224: UserWarning: The weights matrix is not fully connected: 
 There are 59 disconnected components.
 There are 25 islands with ids: 1861678548643203686, 66de0cab-0aca-11e7-82f6-3863bb44ef7c, f3140fb8-347b-4dca-96df-eeef2d1bfc50, bc9c9006-3d40-400d-8b5c-17f56e6dfcee, 956de8aa-9e06-4efb-8eb0-35fe9b274a48, 514f3dda-4d08-464c-b2d4-5706d400065a, ecbfcdb7-fffc-4d45-bed2-1510fd45834d, 3db2fa34-0b56-4644-9ae9-bbee1583e717, 9b7e3b8b-97ef-4038-820c-7cd1c1a34fc7, 1817432233006383832, cd72b9da-b7c6-4785-92b5-0fb2130f0d7b, bb07a569-cc74-439e-b424-916c0304f136, 1869753340438110380, 1856847127505992556, 774c5443-d463-42b3-bfc5-b0ab3c56fe35, 66de482a-0aca-11e7-82f6-3863bb44ef7c, 04d557d6-6bc3-4244-b0f1-81ed1449ccd6, d7632897-a6eb-4f8f-9ab2-c66426620fbf, 4b67c6e0-d603-4fbc-afbe-0b8952f4f7af, 09b00240-4c2a-4900-9d09-f13344461c02, 18267c09-1916-48d8-951c-caf88c89edd1, 66dde559-0aca-11e7-82f6-3863bb44ef7c, 66d

Create concave hulls encompassing poor service stations to represent poor service area

In [21]:
poor_service_area_hulls = []

for component in poor_service_stations__component_5_or_more_nodes['component'].unique():

    component_geom = (
        poor_service_stations__component_5_or_more_nodes
        [
            poor_service_stations__component_5_or_more_nodes['component'] == component
        ]
        .geometry
    )

    component_xy = np.stack([
        component_geom.x.values,
        component_geom.y.values
    ]).T

    component_hull = concave_hull(
        component_xy,
        concavity=1.5
        )
    
    component_polygon = Polygon(component_hull)

    poor_service_area_hulls.append(Polygon(component_hull))

poor_service_areas = gpd.GeoDataFrame(
    geometry=gpd.GeoSeries(poor_service_area_hulls),
    crs=2263
)

poor_service_areas_buffer = gpd.GeoDataFrame(
    geometry=gpd.GeoSeries(poor_service_area_hulls).buffer(500),
    crs=2263
)

view result

In [22]:
m = (
    poor_service_areas_buffer
    .explore(
        tiles='cartodb positron nolabels',
        color='orange'
    )
)

(
    local_moran_by_measure
    .explore(
        m=m,
        tiles='cartodb positron nolabels',
        column='any_high_high',
        cmap=['#4f84bd','#f03813'],
        marker_kwds=dict(
            radius=1
        )
    )
)

m

### save out

In [23]:
poor_service_areas_buffer.to_file('../poor_service_areas_buffer.geojson')